## Draw Figure

In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import os
if not os.path.exists('figs'):
    os.makedirs('figs')
cfdata = pd.read_csv('data/processed_fidelity.csv')
cfdata


layer            pp      shots     fqram
0        2  1.000000e-02    1000000  0.446062
1        3  1.000000e-02    1000000  0.166102
2        4  1.000000e-02    1000000  0.060095
3        5  1.000000e-02    1000000  0.023130
4        6  1.000000e-02    1000000  0.009860
..     ...           ...        ...       ...
107      8  1.000000e-06    5000000  0.995339
108      8  5.000000e-07    5000000  0.997672
109      8  1.000000e-07   10000000  0.999535
110      8  5.000000e-08  100000000  0.999764
111      8  1.000000e-08  500000000  0.999953

[112 rows x 4 columns]

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
fontsize = 55
colors = ['#7895C1','#5CA7C7','#383838','#D4352D','#5CC785','#ADD8E6','#EFD709','#EE8C67']
# Nature期刊格式设置
plt.rcParams.update({
    'font.size': fontsize,
    'font.sans-serif': 'Arial',
    'axes.labelsize': fontsize,
    'axes.titlesize': fontsize,
    'legend.fontsize': fontsize,
    'xtick.labelsize': fontsize,
    'ytick.labelsize': fontsize,
    'lines.markersize': 25,
    'lines.linewidth': 5.0,
    'axes.linewidth': 3,
    'xtick.major.width': 3,
    'xtick.major.size': 15,
    'ytick.major.width': 3,
    'ytick.major.size': 15,
    'xtick.minor.width': 2,
    'xtick.minor.size': 10,
    'ytick.minor.width': 2,
    'ytick.minor.size': 10,
    'figure.dpi': 600,
    "pdf.fonttype": 42,
    "ps.fonttype": 42,
    'figure.figsize': (25*1.5, 24)  # 双栏尺寸：18cm → 7.2 inches
})
from matplotlib.ticker import AutoMinorLocator
from matplotlib.markers import MarkerStyle
## use colormap to represent different layers
import matplotlib.cm as cm
import matplotlib.colors as mcolors
cmap = cm.get_cmap('summer', 8)  # 9个离散颜色
for layer in cfdata['layer'].unique():
    layer_data = cfdata[cfdata['layer'] == layer]
    data = layer_data[(1-layer_data['fqram'])<0.1]
    logpp = np.log(data.pp)
    loginfqram = np.log(1-data.fqram)
    ## fit the curve by numpy ployfit
    # print(pp)
    coefficients= np.polyfit(logpp, loginfqram, 1)
    # print(residual)
    # slope = (1-fqram)/pp
    print(coefficients)
    poly_function = np.poly1d(coefficients)
    r = np.corrcoef(loginfqram, poly_function(logpp))[0, 1]
    # print("r =", r)
    print("R^2 =", r**2)
    y_fit = np.exp(poly_function(logpp))
    plt.plot(layer_data['pp'], 1-layer_data['fqram'],":", marker=MarkerStyle('d', fillstyle='full'), color=cmap(layer-2), label=f'Layer {layer}')
    plt.plot(data['pp'], y_fit, '-', color=cmap(layer-2), label = f'{layer} layers: '+ r"$A=$"+f"{np.exp(coefficients[1]):.1f},"+r"$\alpha=$"+f"{coefficients[0]:.3f}")
## plot the experimental data

plt.grid(which='major',axis='y',linestyle='--',linewidth=2,alpha=0.5)
expdata = [{
    "layer": 2,
    "pp": 0.0038,
    "fqram": 0.595
},{
    "layer": 3,
    "pp": 0.0038,
    "fqram": 0.200
}]
plt.legend()
for item in expdata:
    plt.plot(item['pp'], 1-item['fqram'], '*', color=cmap(item['layer']-2),
             markeredgecolor='white', 
             markeredgewidth=5,
             markersize=60, label=f"Experiment data (Layer {item['layer']})")

## 添加 colormap 图例
plt.xscale('log')
plt.yscale('log')
# 获取当前的 Figure 和 Axes
fig = plt.gcf()  # 获取当前图形 (Figure)
ax = plt.gca()   # 获取当前坐标系 (Axes)
ax.spines['top'].set_visible(False)
ax.spines['right'].set_visible(False)
# 1. 创建 ScalarMappable
sm = cm.ScalarMappable(cmap=cmap, norm=mcolors.Normalize(vmin=1, vmax=9))
sm.set_array([]) 

# 2. 创建一个内嵌的 Axes 来放置 Colorbar
# [left, bottom, width, height]：这些是相对于 Figure 的比例坐标（0.0 到 1.0）
# 根据您的图，我们将其放在底部中央偏左的位置：
# 假设主图 Axes 是 [0.1, 0.1, 0.8, 0.8] 左右
# 我们将 Colorbar 放在 [0.3, 0.15, 0.4, 0.03]
cax = fig.add_axes([0.5, 0.25, 0.33, 0.05]) # 坐标：[左边界, 底边界, 宽度, 高度]

# 3. 添加 Colorbar 到新的 cax
cbar = plt.colorbar(
    sm,
    cax=cax,                      # 将 Colorbar 绘制到内嵌的 Axes (cax) 上
    ticks=range(1, 9),           # 刻度设置在 2, 3, ..., 9
    orientation='horizontal',     # 横向
)

# 4. 调整刻度位置使其居中
# 要让刻度标签位于颜色块中央，需要手动调整刻度位置
# 离散颜色的刻度位置应该在 (刻度值 - 0.5) 和 (刻度值 + 0.5) 之间
# 对于 BoundaryNorm，刻度通常需要移动 0.5。
tick_locations = [t + 0.5 for t in range(1, 9)] # 2.5, 3.5, ..., 8.5
cbar.set_ticks(tick_locations)
cbar.set_ticklabels(range(2, 10)) # 设置标签为 2, 3, ..., 9

# 5. 设置标签和刻度字体
cbar.set_label('Number of layers', fontsize=fontsize)
cbar.ax.tick_params(labelsize=fontsize)

# 6. 设置为无边框
# 移除 Colorbar 的边框线
cbar.outline.set_visible(False) 

ax.set_xlabel('Two qubits gate error rate $p$')
ax.set_ylabel('Infidelity $1-F$')

plt.savefig('figs/ExtendDataFig2.svg', bbox_inches='tight')


/tmp/ipykernel_544885/1678807437.py:35: MatplotlibDeprecationWarning: The get_cmap function was deprecated in Matplotlib 3.7 and will be removed two minor releases later. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap(obj)`` instead.
  cmap = cm.get_cmap('summer', 8)  # 9个离散颜色


[0.99468298 4.55468153]
R^2 = 0.9999797218584483
[0.99699753 5.75444606]
R^2 = 0.9999841169587915
[0.99512737 6.50923803]
R^2 = 0.9999863140881846
[0.9970522  7.13011167]
R^2 = 0.9999723997849529
[0.99415213 7.57849051]
R^2 = 0.9999563325571237
[0.99754371 8.04620127]
R^2 = 0.9999967164759418
[0.99279685 8.65881583]
R^2 = 0.9999471856758917
[0.99430854 8.35827766]
R^2 = 0.9999938754022627


: 

: 

: 